# Lab 7 - Examining Feature Spaces with PCA

## Background

In class, we talked about how machine learning techniques require vectors, and you must first perform **feature extraction** to create **feature vectors** if your data is not already in vector form. I mentioned that this is considered outside the domain of machine learning, but that's not entirely true, especially in recent years. In fact, most modern ML techniques that work on data that's not naturally represented as vectors (e.g., text, images, audio) begin with a very simple vector representation of the raw signal, then **learn** how to extract good features from them.

For example, in computer vision we used to start by detecting corners, edges, or other low-level visual features in images, then shoehorn those into vectors, which we would then use machine learning to classify. Nowadays, we typically flatten the image into a vector (pretty much just `np.flatten`) and use models that learn how to go from raw pixels to the answers we want.

An early example of such a model is called LeNet, and it was designed to work on the handwritten digit recognition problem that we briefly touched on in class. This model works in **layers**, where each layer transforms the image into a new set of features, until finally the last layer spits out a classification; in our case, it's trying to decide which of `range(10)` a handwritten digit represents. Here's a diagram of LeNet- the details aren't important, so don't worry about the specifics - but notice that the model is drawn in layers: ![](https://facultyweb.cs.wwu.edu/~wehrwes/courses/data311_21f/lab7/lenet5.png)

When trained well, the practical effect of models like this (these are called "convolutional neural networks", by the way) is that **the features become more and more "well-organized" after each layer**. Unfortunately, each intermediate feature representation is high-dimensional, so we can't directly see this. One of the uses we discussed in class for PCA is for visualizing high-dimensional things. In this lab, we're going to put this to use to visualize the the features at each step and see if we observe a trend towards a more orderly set of features.

Let's get some useful imports out of the way - if you need more libraries, import them here:

In [ ]:
import numpy as np
import pandas as pd
import requests
import io
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.decomposition import PCA

## The Data

For our purposes, the code for the LeNet model can be abstracted to something like this:

```python
inputs = load_digits()
conv1_features = conv1(inputs)
conv2_features = conv2(conv1_features)
fc1_features = fc1(conv2_features)
fc2_features = fc2(fc1_features)
fc3_features = fc3(fc2_features)
```

The specifics of the functions aren't important to us right now. Notice that each function simply takes the output of the prior one, and transforms it in some way to produce the next set of features.

Let's load up two files that give us access to those variables above, as well as the ground-truth digit labels, for 5400 example digits:

In [ ]:
# adapted from https://stackoverflow.com/a/61716809
def np_load_from_url(url):
    response = requests.get(url)
    response.raise_for_status() # throw an error if it didn't work
    return np.load(io.BytesIO(response.content))

In [ ]:
base_url = "https://facultyweb.cs.wwu.edu/~wehrwes/courses/data311_21f/data/mnist/"
labels = np_load_from_url(base_url + "labels.npz")["labels"]
features = dict(np_load_from_url(base_url + "features.npz"))

In [ ]:
print(labels.shape, labels[:10])

We can see that there are 5400 labels, and each one says what digit a given example actually represents.

In [ ]:
print(features.keys())

The `features` dict contains values for each of the variables described in the pseudocode above. The `input` just contains the input images, flattened into vectors:

In [ ]:
features["input"].shape

Notice this is, as per tradition, an $n \times d$ matrix - each of 5400 images have 784 pixels (originally, they were 28x28). We can visualize a few images to see what they look like:

In [ ]:
fig = plt.figure(figsize=(10, 4))
for i in range(10):
    plt.subplot(1,10,i+1)
    in_image = features["input"][i].reshape((28, 28))
    plt.imshow(in_image, cmap="gray")
    plt.title(str(labels[i]))

Notice the labels (above each image) line up with the labels we saw above.

The remaining features don't have such a nice visualizeable interpretation - we're stuck just thinking of them as high-dimensional vectors. Let's see their dimensionality:

In [ ]:
pd.DataFrame({"Feature set" : features.keys(),
              "Shape": [f.shape for f in features.values()]})

## Your Tasks

#### Part 1: Visualizing the Feature Spaces

**1.1**: Your first (and primary) job in part 1 is to take each of these collections of feature vectors (I'll call them "feature sets" from here on out), use PCA to reduce their dimensionality to two, transform the features into their 2D representation, and visualize them in a scatterplot; color-code the points in the scatterplot by the ground-truth label (stored in `labels`).

##### PCA Refresher
Recall that you can compute PCA using `scikit-learn` by instantiating a `PCA` object, passing it the number of components you want to fit:
```python
pca = PCA(n_components=d_prime)
```
then calling its `fit` method on the $n \times d$ data matrix:
```python
pca.fit(X)
```

This computes the `d_prime` component vectors that point in the directions of greatest variance, accessible via `pca.components_`. To actually reduce the dimensionality of the data, you can convert your data matrix into a new `d_prime`-dimensional data matrix (which lives in the space spanned by the `d_prime` component vectors). In `sklearn`, you can accomplish this using the PCA object's `transform` method:
```python
Xprime = pca.transform(X)
```
where `Xprime.shape` would now be `(n, d_prime)`. You can access the fraction of variance explained by each component using `pca.explained_variance_ratio_`.

In [ ]:
# TODO 1.1 - your code here

**1.2** You'll notice that in the plot for the final feature set (`fc3`), there is still considerable overlap among points in different classses. Does this imply that if we run some kind of classification or clustering scheme on these feature vectors, we should expect it to be impossible to get very high accuracy? Why or why not?

**TODO 1.2** - Write your answer to part 2.2 here.

#### Part 2: Estimating Intrinsic Dimensionality

Above, we used PCA to visualize how "orderly" the feature space is as it goes through the model. Now, let's look at this in a slightly more quantitative way. We talked about **intrinsic dimensionality** as the minimum number of dimensions needed to represent a set of data. PCA also gives us a coarse way to estimate the intrinsic dimensionality by looking at the amount of variance explained by each component. For example, if the vast majority of the variance is explained by the first two components, the intrinsic dimensionality is probably around 2.

**2.1**: For each of the feature sets, compute up to 100 PCA components (for features with $d < 100$, compute all $d$ components) and make a plot to visualize the fraction of the variance explained by each of the first K components as a function of K (you may find the `np.cumsum` function helpful here).

**2.2**: Let's (arbitrarily) define our estimate of intrinsic dimensionality to be the number of components needed to explain at least 90% of the variance. For each feature set, what is its intrinsic dimensionality esimate based on this definitions? Show your results in a nicely formatted table and/or a sensibly designed plot.

In [ ]:
# TODO 2.1 and 2.2 - your code and results here

#### Extra Credit

Use K-Means clustering to cluster the vectors in each feature set. Visualize the clustering results vs. the ground truth labels (you'll need to use PCA to reduce the dimensionality after clustering). Finally, calculate the percentage of digits that were assigned to a "correct" cluster. Note that since the clustering does not know anything about the actual digit labels, you'll need to find some way to establish correspondence between cluster labels and ground truth labels.